In [0]:
spark

SparkSession - hive 
 
 
 SparkContext 

 Spark UI 

 
 Version 
 v3.3.2 
 Master 
 local[8] 
 AppName 
 Databricks Shell

In [0]:
pip install nltk

Python interpreter will be restarted.
Python interpreter will be restarted.


In [0]:
import re
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

# Download NLTK stopwords if not already downloaded
import nltk
nltk.download('stopwords')
nltk.download('punkt')

# Get NLTK English stopwords
stop_words = set(stopwords.words('english'))


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [0]:
%fs ls /FileStore/tables/wiki_small.csv

path name size modificationTime dbfs:/FileStore/tables/wiki_small.csv wiki_small.csv 985338 1717040693000

In [0]:
sc= spark.sparkContext

In [0]:
#reading the wikipedia data, it contains the wiki page link and the text content of that page

wiki= sc.textFile("/FileStore/tables/wiki_small.csv")

#seeing the entries of the data
wiki.take(3)

Out[3]: ['url,text',
 'https://simple.wikipedia.org/wiki/Carl%20Vinson,Carl Vinson November    June   was an American politician. He served as a Representative from Georgia. He was a Democrat. He was the first person to serve for more than  years in the United States House of Representatives. He was known as The Father of the TwoOcean Navy.Other websites University of Georgia brief biography  University of Georgia Profile of Carl Vinson  Congressional Biography entry in the New Georgia Encyclopedia   United States Navy website  USS CARL VINSON  Mercer University Press Carl Vinson Patriarch of the Armed Forces   Vinson Institute Press Carl Vinson  A Legacy of Public Service   births deathsDeans of the United States House of RepresentativesUnited States representatives from GeorgiaUS Democratic Party politiciansthcentury American politicians',
 'https://simple.wikipedia.org/wiki/Oberhasli%20%28district%29,The district of Oberhasli in the Swiss canton of Bern has  municipalities in an are

In [0]:
wiki.first()

Out[4]: 'url,text'

In [0]:
#there are these many entries
wiki.count()

Out[5]: 1001

In [0]:
#function to clean the text in the data
def clean_text(text):
    text = re.sub(r'\.', ' ', text)
    # Remove punctuation and numbers
    cleaned_text = re.sub(r'[^\w\s]', '', text)
    cleaned_text = re.sub(r'\d+', '', cleaned_text)
    
    # Remove stopwords
    cleaned_text = ' '.join(word.lower() for word in cleaned_text.split() if word.lower() not in stop_words)
    
    return cleaned_text

In [0]:
#testing the clean text function

clean_text("Carl Vinson November78 $&*##   June   was an American politician. He served as a Representative from Georgia. He was a Democrat. He was the first person to serve for more than  years in the United States House of Representatives.")

Out[7]: 'carl vinson november june american politician served representative georgia democrat first person serve years united states house representatives'

In [0]:
# Applying the clean text function to wiki data
wiki = wiki.map(lambda x: x.split(',')[0] + ',' + clean_text(x.split(',')[1]))
wiki.take(4)

Out[8]: ['url,text',
 'https://simple.wikipedia.org/wiki/Carl%20Vinson,carl vinson november june american politician served representative georgia democrat first person serve years united states house representatives known father twoocean navy websites university georgia brief biography university georgia profile carl vinson congressional biography entry new georgia encyclopedia united states navy website uss carl vinson mercer university press carl vinson patriarch armed forces vinson institute press carl vinson legacy public service births deathsdeans united states house representativesunited states representatives georgiaus democratic party politiciansthcentury american politicians',
 'https://simple.wikipedia.org/wiki/Oberhasli%20%28district%29,district oberhasli swiss canton bern municipalities area km oberhasli',
 'https://simple.wikipedia.org/wiki/Norman%2C%20Arkansas,norman town us state arkansas towns arkansas']

In [0]:
#function to tokenize the data

def tokenize (line):
    url, text = line.split(",")

    return (url, text)

In [0]:
wiki_recs=wiki.map(lambda line: tokenize(line))
#wiki_recs=wiki.map(tokenize)   --- same 

In [0]:
wiki_recs
wiki_recs.take(3)

Out[11]: [('url', 'text'),
 ('https://simple.wikipedia.org/wiki/Carl%20Vinson',
  'carl vinson november june american politician served representative georgia democrat first person serve years united states house representatives known father twoocean navy websites university georgia brief biography university georgia profile carl vinson congressional biography entry new georgia encyclopedia united states navy website uss carl vinson mercer university press carl vinson patriarch armed forces vinson institute press carl vinson legacy public service births deathsdeans united states house representativesunited states representatives georgiaus democratic party politiciansthcentury american politicians'),
 ('https://simple.wikipedia.org/wiki/Oberhasli%20%28district%29',
  'district oberhasli swiss canton bern municipalities area km oberhasli')]

In [0]:
#unigram function
def unigram(url, text, n=1):
    tokens= text.split()
    return [(tok.lower(), url) for tok in tokens ]


In [0]:
def bigram(url, text):
    tokens = text.split()
    bigrams = [(tokens[i].lower(), tokens[i+1].lower(), url) for i in range(len(tokens)-1)]
    return bigrams


In [0]:
unigram("url1", "This is a test case")

Out[14]: [('this', 'url1'),
 ('is', 'url1'),
 ('a', 'url1'),
 ('test', 'url1'),
 ('case', 'url1')]

In [0]:
bigram("url1", "This is a test case")

Out[15]: [('this', 'is', 'url1'),
 ('is', 'a', 'url1'),
 ('a', 'test', 'url1'),
 ('test', 'case', 'url1')]

In [0]:
wiki_index= wiki_recs.flatMap(lambda rec: unigram(rec[0], rec[1]))

In [0]:
#wiki_index= wiki_recs.flatMap(lambda rec: bigram(rec[0], rec[1]))
#wiki_index.take(10)

In [0]:
wiki_index.take(10)

Out[18]: [('text', 'url'),
 ('carl', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('vinson', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('november', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('june', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('american', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('politician', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('served', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('representative', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('georgia', 'https://simple.wikipedia.org/wiki/Carl%20Vinson')]

In [0]:
wiki_index.count()

Out[19]: 90969

In [0]:
header= wiki_index.first()

In [0]:
wiki_index= wiki_index.filter(lambda rec: rec!=header)
wiki_index.take(10)

Out[21]: [('carl', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('vinson', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('november', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('june', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('american', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('politician', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('served', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('representative', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('georgia', 'https://simple.wikipedia.org/wiki/Carl%20Vinson'),
 ('democrat', 'https://simple.wikipedia.org/wiki/Carl%20Vinson')]

In [0]:
#group the URLs by the key (word)
wiki_inverted_index= wiki_index.groupByKey().mapValues(list)

In [0]:
wiki_inverted_index.take(1)

Out[23]: [('carl',
  ['https://simple.wikipedia.org/wiki/Carl%20Vinson',
   'https://simple.wikipedia.org/wiki/Carl%20Vinson',
   'https://simple.wikipedia.org/wiki/Carl%20Vinson',
   'https://simple.wikipedia.org/wiki/Carl%20Vinson',
   'https://simple.wikipedia.org/wiki/Carl%20Vinson',
   'https://simple.wikipedia.org/wiki/Carl%20Tacy',
   'https://simple.wikipedia.org/wiki/1984%20State%20of%20the%20Union%20Address',
   'https://simple.wikipedia.org/wiki/November%2028',
   'https://simple.wikipedia.org/wiki/Silly%20Symphony'])]

In [0]:
wiki_inverted_index= wiki_index.groupByKey().mapValues(set)
wiki_inverted_index.take(1)

Out[24]: [('carl',
  {'https://simple.wikipedia.org/wiki/1984%20State%20of%20the%20Union%20Address',
   'https://simple.wikipedia.org/wiki/Carl%20Tacy',
   'https://simple.wikipedia.org/wiki/Carl%20Vinson',
   'https://simple.wikipedia.org/wiki/November%2028',
   'https://simple.wikipedia.org/wiki/Silly%20Symphony'})]

In [0]:
wiki_inverted_index= (  wiki_inverted_index
                      .map(lambda rec: (rec[0], list(rec[1])   )) )

In [0]:
wiki_inverted_index.take(1)

Out[26]: [('carl',
  ['https://simple.wikipedia.org/wiki/Carl%20Tacy',
   'https://simple.wikipedia.org/wiki/Silly%20Symphony',
   'https://simple.wikipedia.org/wiki/Carl%20Vinson',
   'https://simple.wikipedia.org/wiki/1984%20State%20of%20the%20Union%20Address',
   'https://simple.wikipedia.org/wiki/November%2028'])]

In [0]:
filepath=("/FileStore/tables/wiki_small.csv")

In [0]:
wiki_indexes = (sc
    .textFile(filepath)
    .map(lambda x: x.split(',')[0] + ',' + clean_text(x.split(',')[1]))
    .map(tokenize)
    .flatMap(lambda rec: unigram(rec[0], rec[1]))
    .groupByKey()
    .mapValues(set)
    .map(lambda x: (x[0], list(x[1])))
    .sortByKey()
)

In [0]:
wiki_indexes.take(10)

Out[29]: [('aaa', ['https://simple.wikipedia.org/wiki/Deaths%20in%20May%202017']),
 ('aachen', ['https://simple.wikipedia.org/wiki/St.%20Anthony-Chapel']),
 ('aachenbuildings',
  ['https://simple.wikipedia.org/wiki/St.%20Anthony-Chapel']),
 ('aadhinatha', ['https://simple.wikipedia.org/wiki/Viluppuram']),
 ('aadhinathan', ['https://simple.wikipedia.org/wiki/Viluppuram']),
 ('aamras', ['https://simple.wikipedia.org/wiki/Aamras']),
 ('aamrasfruits', ['https://simple.wikipedia.org/wiki/Aamras']),
 ('aapke', ['https://simple.wikipedia.org/wiki/Deaths%20in%20May%202017']),
 ('aargau', ['https://simple.wikipedia.org/wiki/Sch%C3%B6ftland']),
 ('aau',
  ['https://simple.wikipedia.org/wiki/Association%20of%20American%20Universities',
   'https://simple.wikipedia.org/wiki/Amateur%20Athletic%20Union'])]

In [0]:
wiki_info= wiki_indexes.collect()
display(wiki_info)

_1 _2 aaa List(https://simple.wikipedia.org/wiki/Deaths%20in%20May%202017) aachen List(https://simple.wikipedia.org/wiki/St.%20Anthony-Chapel) aachenbuildings List(https://simple.wikipedia.org/wiki/St.%20Anthony-Chapel) aadhinatha List(https://simple.wikipedia.org/wiki/Viluppuram) aadhinathan List(https://simple.wikipedia.org/wiki/Viluppuram) aamras List(https://simple.wikipedia.org/wiki/Aamras) aamrasfruits List(https://simple.wikipedia.org/wiki/Aamras) aapke List(https://simple.wikipedia.org/wiki/Deaths%20in%20May%202017) aargau List(https://simple.wikipedia.org/wiki/Sch%C3%B6ftland) aau List(https://simple.wikipedia.org/wiki/Association%20of%20American%20Universities, https://simple.wikipedia.org/wiki/Amateur%20Athletic%20Union) ababa List(https://simple.wikipedia.org/wiki/Tekeda%20Alemu, https://simple.wikipedia.org/wiki/Dire%20Dawa) abacus List(https://simple.wikipedia.org/wiki/Analogue%20computer) abala List(https://simple.wikipedia.org/wiki/2018%20FIFA%20World%20Cup%20qualification%20%E2%80%93%20UEFA%20Group%20B) abandon List(https://simple.wikipedia.org/wiki/John%20Smith%20%28explorer%29) abandoned List(https://simple.wikipedia.org/wiki/Linn%20County%2C%20Kansas) abandoning List(https://simple.wikipedia.org/wiki/Defection) abandons List(https://simple.wikipedia.org/wiki/Power%20Rangers%20Dino%20Charge) abba List(https://simple.wikipedia.org/wiki/Cover%20version) abbas List(https://simple.wikipedia.org/wiki/Deaths%20in%20May%202017) abbe List(https://simple.wikipedia.org/wiki/Abbeville%2C%20Alabama) abbeville List(https://simple.wikipedia.org/wiki/Abbeville%2C%20Alabama) abbey List(https://simple.wikipedia.org/wiki/Melk, https://simple.wikipedia.org/wiki/Princess%20Anne%20of%20England, https://simple.wikipedia.org/wiki/Henry%20III%20of%20England, https://simple.wikipedia.org/wiki/St.%20Anthony-Chapel, https://simple.wikipedia.org/wiki/Roger%20I%20de%20Montgomery, https://simple.wikipedia.org/wiki/James%20Butler%2C%201st%20Duke%20of%20Ormonde) abbeybritish List(https://simple.wikipedia.org/wiki/James%20Butler%2C%201st%20Duke%20of%20Ormonde) abbot List(https://simple.wikipedia.org/wiki/St.%20Anthony-Chapel, https://simple.wikipedia.org/wiki/James%20Butler%2C%201st%20Duke%20of%20Ormonde, https://simple.wikipedia.org/wiki/Mirande) abbots List(https://simple.wikipedia.org/wiki/History%20of%20the%20Catholic%20Church) abbott List(https://simple.wikipedia.org/wiki/Chancellor%20of%20the%20Exchequer) abbottabad List(https://simple.wikipedia.org/wiki/Dalola) abbreviated List(https://simple.wikipedia.org/wiki/Gaius, https://simple.wikipedia.org/wiki/Heard%20Island%20and%20McDonald%20Islands, https://simple.wikipedia.org/wiki/Hypertext%20Transfer%20Protocol, https://simple.wikipedia.org/wiki/Mound%20City%2C%20Kansas) abbreviation List(https://simple.wikipedia.org/wiki/Cuba%20at%20the%20Olympics, https://simple.wikipedia.org/wiki/Gaius) abby List(https://simple.wikipedia.org/wiki/Ashley%20Hinson) abc List(https://simple.wikipedia.org/wiki/Australian%20Overland%20Telegraph%20Line, https://simple.wikipedia.org/wiki/Lana%20Parrilla, https://simple.wikipedia.org/wiki/The%20Chew, https://simple.wikipedia.org/wiki/Carter%20Blackburn, https://simple.wikipedia.org/wiki/Factorial, https://simple.wikipedia.org/wiki/Make%20It%20or%20Break%20It, https://simple.wikipedia.org/wiki/Jim%20Lampley) abcdefghjk List(https://simple.wikipedia.org/wiki/Model%20Town%20Lahore) abdelkader List(https://simple.wikipedia.org/wiki/Council%20of%20the%20Nation) abdicate List(https://simple.wikipedia.org/wiki/Mary%2C%20Queen%20of%20Scots) abdicated List(https://simple.wikipedia.org/wiki/Insei) abdomen List(https://simple.wikipedia.org/wiki/Bret%20Hart, https://simple.wikipedia.org/wiki/Colitis) abducted List(https://simple.wikipedia.org/wiki/The%20Dark%20Knight%20Rises) abdul List(https://simple.wikipedia.org/wiki/Gopal%20Ballav%20Pattanaik, https://simple.wikipedia.org/wiki/November%2028) abdulaziz List(https://simple.wikipedia.org/wiki/Deaths%20in%20May%202017) a